In [1]:
import pandas as pd
from sklearn.model_selection import train_test_split, StratifiedKFold
import numpy as np
import matplotlib.pyplot as plt
import torch
import torch.nn as nn
import torch.nn.functional as F
from imblearn.over_sampling import SMOTE
from sklearn.metrics import accuracy_score

# Stratified Train Test Split

In [2]:
# Importing pre-processed dataset
diabetes_df = pd.read_csv('processed_diabetes_dataset.csv')

In [3]:
# Acquiring target values and attributes
y = diabetes_df['Diabetes'].values
y = np.float32(y)
X = diabetes_df.drop(columns=['Diabetes']).values
X = np.float32(X)

In [4]:
input_dim = X.shape[1] # NN input dimension = number of attributes

In [5]:
# Performing stratified train test split where test set is 30% of dataset
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=42, shuffle=True, stratify=y)

# SMOTE

In [6]:
# sm = SMOTE(sampling_strategy=smote_ratio, random_state=42)
# X_res, y_res = sm.fit_resample(X, y)

# Multi-Layered Perceptron (MLP)

In [7]:
class MLP_network(nn.Module):
    def __init__(self, input_dim=input_dim, hidden_dim=10, output_dim=1, extra_hidden_layers=0):
        super(MLP_network, self).__init__()
        layers = []
        layers.append(nn.Linear(input_dim, hidden_dim, bias=True))
        layers.append(nn.ReLU())
        for i in range(extra_hidden_layers):
            layers.append(nn.Linear(hidden_dim, hidden_dim, bias=True))
            layers.append(nn.ReLU())
        layers.append(nn.Linear(hidden_dim, output_dim, bias=True))
        self.output = nn.Sequential(*layers)

    def forward(self, X, **kwargs):
        # sigmoid activation function is applied in loss function, so it is excluded here
        return self.output(X)

In [8]:
class MLP_network2(nn.Module):
    def __init__(self, input_dim=input_dim, hidden_dim=10, output_dim=1):
        super().__init__()
        self.hidden1 = nn.Linear(input_dim, hidden_dim, bias=True)
        self.hidden2 = nn.Linear(hidden_dim, hidden_dim, bias=True)
        self.hidden3 = nn.Linear(hidden_dim, hidden_dim, bias=True)
        self.output = nn.Linear(hidden_dim, output_dim, bias=True)

    def forward(self, X):
        X = F.relu(self.hidden1(X))
        X = F.relu(self.hidden2(X))
        X = F.relu(self.hidden3(X))
        # sigmoid activation function is applied in loss function, so it is excluded here
        return self.output(X)

# Hyperparameter Tuning with Optuna

In [9]:
from skorch.classifier import NeuralNetBinaryClassifier
from skorch.callbacks import EarlyStopping
import optuna
from optuna.integration import SkorchPruningCallback

In [10]:
early_stopping = EarlyStopping(monitor='valid_acc', patience=10)

In [11]:
def objective(trial):
    
    hidden_dim = trial.suggest_int('hidden_dim', 4, input_dim*2)
    extra_hidden_layers = trial.suggest_int('extra_hidden_layers', 0, 5)
    batch_size = trial.suggest_categorical('batch_size', [64, 128, 256, 512])
    learning_rate = trial.suggest_float('learning_rate', 0.0001, 0.1)
    weight_decay = trial.suggest_float('weight_decay', 0.0001, 0.1)
    smote_ratio = trial.suggest_float('smote_ratio', 0.6, 1.)
    max_epochs = trial.suggest_int('max_epochs', 50, 200, 10)

    
    torch.manual_seed(0)
    net = NeuralNetBinaryClassifier(
        MLP_network(),
        module__hidden_dim=hidden_dim,
        module__extra_hidden_layers=extra_hidden_layers,
        criterion=torch.nn.BCEWithLogitsLoss,
        optimizer=torch.optim.SGD,
        optimizer__momentum=0.9, # momentum set to commonly used value to save CPU time
        optimizer__lr=learning_rate,
        optimizer__weight_decay=weight_decay,
        max_epochs=max_epochs,
        batch_size=batch_size,
        callbacks=[SkorchPruningCallback(trial, 'valid_acc'), early_stopping],
    )
    
    
    sm = SMOTE(sampling_strategy=smote_ratio, random_state=42)
    X_resampled, y_resampled = sm.fit_resample(X_train, y_train)
    
    
    net.fit(X_resampled, y_resampled)
    y_pred = net.predict(X_test)
    return accuracy_score(y_test, y_pred)

In [11]:
def objective(trial):
    
    hidden_dim = trial.suggest_int('hidden_dim', 4, input_dim*2)
    batch_size = trial.suggest_categorical('batch_size', [64, 128, 256, 512])
    learning_rate = trial.suggest_float('learning_rate', 0.0001, 0.1)
    weight_decay = trial.suggest_float('weight_decay', 0.0001, 0.1)
    smote_ratio = trial.suggest_float('smote_ratio', 0.6, 1.)
    max_epochs = trial.suggest_int('max_epochs', 50, 200, 10)

    
    torch.manual_seed(0)
    net = NeuralNetBinaryClassifier(
        MLP_network2(),
        module__hidden_dim=hidden_dim,
        criterion=torch.nn.BCEWithLogitsLoss,
        optimizer=torch.optim.SGD,
        optimizer__momentum=0.9, # momentum set to commonly used value to save CPU time
        optimizer__lr=learning_rate,
        optimizer__weight_decay=weight_decay,
        max_epochs=max_epochs,
        batch_size=batch_size,
        callbacks=[SkorchPruningCallback(trial, 'valid_acc'), early_stopping],
    )
    
    
    sm = SMOTE(sampling_strategy=smote_ratio, random_state=42)
    X_resampled, y_resampled = sm.fit_resample(X_train, y_train)
    
    
    net.fit(X_resampled, y_resampled)
    y_pred = net.predict(X_test)
    return accuracy_score(y_test, y_pred)

In [12]:
pruner = optuna.pruners.MedianPruner(n_warmup_steps=30)
study = optuna.study.create_study(direction="maximize", pruner=pruner)
study.optimize(objective, n_trials=300)

[I 2022-04-30 11:14:44,696] A new study created in memory with name: no-name-e9b533f5-feb6-4eff-b1ff-d015d3dedd00


  epoch    train_loss    valid_acc    valid_loss     dur
-------  ------------  -----------  ------------  ------
      1        0.2389       0.4402        1.1266  2.3052
      2        0.4352       0.4402        1.1115  2.4064
      3        0.4350       0.4402        1.1115  2.3284
      4        0.4350       0.4402        1.1115  2.3585
      5        0.4350       0.4402        1.1115  2.3675
      6        0.4350       0.4402        1.1115  2.3510
      7        0.4350       0.4402        1.1115  2.3245
      8        0.4350       0.4402        1.1115  2.3652
      9        0.4350       0.4402        1.1115  2.3522
     10        0.4350       0.4402        1.1115  2.4035
Stopping since valid_acc has not improved in the last 10 epochs.


[I 2022-04-30 11:15:26,307] Trial 0 finished with value: 0.15758698622937034 and parameters: {'hidden_dim': 16, 'extra_hidden_layers': 3, 'batch_size': 512, 'learning_rate': 0.00763808929678378, 'weight_decay': 0.08637439324246071, 'smote_ratio': 0.7863382966767648, 'max_epochs': 70}. Best is trial 0 with value: 0.15758698622937034.


  epoch    train_loss    valid_acc    valid_loss     dur
-------  ------------  -----------  ------------  ------
      1        0.1972       0.3969        1.1979  2.6151
      2        0.2646       0.3969        1.1979  2.5261
      3        0.2646       0.3969        1.1979  2.4201
      4        0.2646       0.3969        1.1979  2.5116
      5        0.2646       0.3969        1.1979  2.4386
      6        0.2646       0.3969        1.1979  2.4391
      7        0.2646       0.3969        1.1979  2.4743
      8        0.2646       0.3969        1.1979  2.4405
      9        0.2646       0.3969        1.1979  2.4256
     10        0.2646       0.3969        1.1979  2.5236
Stopping since valid_acc has not improved in the last 10 epochs.


[I 2022-04-30 11:16:09,221] Trial 1 finished with value: 0.15758698622937034 and parameters: {'hidden_dim': 14, 'extra_hidden_layers': 2, 'batch_size': 256, 'learning_rate': 0.07390047602689435, 'weight_decay': 0.08946652949278389, 'smote_ratio': 0.6580871491317536, 'max_epochs': 60}. Best is trial 0 with value: 0.15758698622937034.


  epoch    train_loss    valid_acc    valid_loss     dur
-------  ------------  -----------  ------------  ------
      1        0.1645       0.4599        1.7081  2.4654
      2        0.4009       0.4599        1.5077  2.4817
      3        0.4051       0.4599        1.5076  2.6124
      4        0.4051       0.4599        1.5076  2.4836
      5        0.4051       0.4599        1.5076  2.5166
      6        0.4051       0.4599        1.5076  2.5596
      7        0.4051       0.4599        1.5076  2.4686
      8        0.4051       0.4599        1.5076  2.5306
      9        0.4051       0.4599        1.5076  2.5126


[I 2022-04-30 11:16:49,704] Trial 2 finished with value: 0.15758698622937034 and parameters: {'hidden_dim': 11, 'extra_hidden_layers': 4, 'batch_size': 512, 'learning_rate': 0.012159331162933468, 'weight_decay': 0.01663734122190366, 'smote_ratio': 0.8516496342593927, 'max_epochs': 170}. Best is trial 0 with value: 0.15758698622937034.


KeyboardInterrupt: 

In [ ]:
fig = optuna.visualization.plot_intermediate_values(study)
fig.show()

# Hyperparameter Grid Search

In [16]:
from skorch.classifier import NeuralNetBinaryClassifier
from sklearn.model_selection import GridSearchCV

In [9]:
torch.manual_seed(0)

net = NeuralNetBinaryClassifier(
    MLP_network,
    train_split=None,
    criterion=torch.nn.BCEWithLogitsLoss,
    optimizer=torch.optim.SGD,
    optimizer__momentum=0.9 # momentum set to commonly used value to save CPU time
)

In [10]:
parameters = {
    'max_epochs': [10, 20, 30, 40, 50],
    'batch_size': [64, 128, 256], # batch-sizes are powers of 2
    'optimizer__lr': [0.001, 0.01, 0.1], # common values for learning rate
    'optimizer__weight_decay': [0.001, 0.01, 0.1], # common values for weight-decay factor
    'module__hidden_dim': [5, 10, 15, 20] # range of values less than twice the input dimension
}
gs = GridSearchCV(net, parameters, refit=False, cv=5, scoring='accuracy')
gs.fit(X_train, y_train)
print('Best-performing parameters:', gs.best_params_)
print('5-fold CV score:', gs.best_score_)

  epoch    train_loss    valid_acc    valid_loss     dur
-------  ------------  -----------  ------------  ------
      1        0.7022       0.5176        0.6977  0.0880
      2        0.6920       0.5176        0.6876  0.0880
      3        0.6805       0.5187        0.6747  0.0920
      4        0.6646       0.7099        0.6566  0.0820
      5        0.6425       0.8066        0.6329  0.0820
      6        0.6155       0.7813        0.6052  0.0880
      7        0.5841       0.8077        0.5731  0.0850
      8        0.5489       0.8363        0.5387  0.0780
      9        0.5116       0.8462        0.5029  0.0770
     10        0.4740       0.8571        0.4673  0.0790
  epoch    train_loss    valid_acc    valid_loss     dur
-------  ------------  -----------  ------------  ------
      1        0.6918       0.5187        0.6915  0.0770
      2        0.6913       0.5187        0.6909  0.0780
      3        0.6905       0.5176        0.6900  0.0700
      4        0.6896       0.5

     10        0.6269       0.7253        0.6134  0.0750
  epoch    train_loss    valid_acc    valid_loss     dur
-------  ------------  -----------  ------------  ------
      1        0.7096       0.4824        0.7033  0.0770
      2        0.6963       0.4824        0.6911  0.0820
      3        0.6839       0.4846        0.6788  0.0960
      4        0.6699       0.5352        0.6638  0.0930
      5        0.6516       0.6868        0.6428  0.0830
      6        0.6266       0.7846        0.6141  0.0740
      7        0.5930       0.8341        0.5759  0.0750
      8        0.5491       0.8495        0.5276  0.0770
      9        0.4963       0.8527        0.4737  0.0750
     10        0.4416       0.8615        0.4228  0.0700
  epoch    train_loss    valid_acc    valid_loss     dur
-------  ------------  -----------  ------------  ------
      1        0.7295       0.4824        0.7106  0.0750
      2        0.7021       0.4824        0.6943  0.0740
      3        0.6893       0.4

      8        0.1162       0.9505        0.1229  0.0710
      9        0.0961       0.9571        0.1052  0.0700
     10        0.0808       0.9703        0.0909  0.0730
  epoch    train_loss    valid_acc    valid_loss     dur
-------  ------------  -----------  ------------  ------
      1        0.6663       0.7505        0.5989  0.0790
      2        0.4407       0.8846        0.3209  0.0680
      3        0.2416       0.9176        0.2213  0.0750
      4        0.1771       0.9253        0.1779  0.0720
      5        0.1467       0.9385        0.1487  0.0710
      6        0.1247       0.9462        0.1242  0.0770
      7        0.1051       0.9604        0.1023  0.0780
      8        0.0873       0.9659        0.0839  0.0690
      9        0.0724       0.9714        0.0685  0.0740
     10        0.0589       0.9769        0.0556  0.0740
  epoch    train_loss    valid_acc    valid_loss     dur
-------  ------------  -----------  ------------  ------
      1        0.6048       0.8

      4        0.3760       0.9022        0.3633  0.0680
      5        0.3256       0.9099        0.3237  0.0700
      6        0.2930       0.9121        0.3004  0.0760
      7        0.2751       0.9143        0.2888  0.0680
      8        0.2657       0.9143        0.2826  0.0710
      9        0.2604       0.9143        0.2789  0.0820
     10        0.2571       0.9143        0.2766  0.0690
  epoch    train_loss    valid_acc    valid_loss     dur
-------  ------------  -----------  ------------  ------
      1        0.6957       0.5176        0.6912  0.0750
      2        0.6905       0.5176        0.6895  0.0700
      3        0.6873       0.6308        0.6835  0.0670
      4        0.6723       0.7352        0.6486  0.0780
      5        0.5953       0.8143        0.5210  0.0780
      6        0.4701       0.8824        0.4331  0.0840
      7        0.4039       0.9022        0.3927  0.0820
      8        0.3739       0.9143        0.3735  0.0810
      9        0.3598       0.9

      6        0.0778       0.9846        0.0718  0.0770
      7        0.1012       0.7132        0.3841  0.0730
      8        0.2434       0.9352        0.1430  0.0770
      9        0.1224       0.8813        0.2155  0.0730
     10        0.1114       0.9681        0.0925  0.0800
  epoch    train_loss    valid_acc    valid_loss     dur
-------  ------------  -----------  ------------  ------
      1        0.4509       0.8692        0.3137  0.0750
      2        0.2132       0.8857        0.3250  0.0730
      3        0.2040       0.9286        0.1706  0.0710
      4        0.1520       0.8538        0.4704  0.0770
      5        0.1910       0.9407        0.1462  0.0750
      6        0.1251       0.9319        0.1438  0.0760
      7        0.1279       0.9341        0.1362  0.0800
      8        0.1369       0.6363        0.4259  0.0820
      9        0.2959       0.9209        0.2246  0.0770
     10        0.2441       0.9077        0.2866  0.0760
  epoch    train_loss    valid_

...

     43        0.0026       1.0000        0.0029  0.0460
     44        0.0026       1.0000        0.0029  0.0460
     45        0.0026       1.0000        0.0029  0.0480
     46        0.0026       1.0000        0.0029  0.0460
     47        0.0026       1.0000        0.0029  0.0500
     48        0.0026       1.0000        0.0029  0.0480
     49        0.0025       1.0000        0.0029  0.0470
     50        0.0025       1.0000        0.0029  0.0470
  epoch    train_loss    valid_acc    valid_loss     dur
-------  ------------  -----------  ------------  ------
      1        0.5611       0.8560        0.3523  0.0460
      2        0.2607       0.9374        0.2015  0.0490
      3        0.1578       0.9297        0.1886  0.0480
      4        0.1136       0.9374        0.1263  0.0470
      5        0.0825       0.9659        0.1040  0.0480
      6        0.0568       0.9758        0.0537  0.0450
      7        0.0362       0.9846        0.0390  0.0440
      8        0.0242       0.9

      2        0.2486       0.9253        0.1961  0.0480
      3        0.1388       0.9538        0.1283  0.0460
      4        0.0869       0.9758        0.0826  0.0510
      5        0.0611       0.9758        0.0723  0.0450
      6        0.0816       0.9549        0.1404  0.0450
      7        0.0482       0.9824        0.0812  0.0460
      8        0.0278       0.9868        0.0516  0.0520
      9        0.0315       0.9165        0.2808  0.0450
     10        0.2383       0.9429        0.1474  0.0490
     11        0.0980       0.9703        0.0767  0.0470
     12        0.0470       0.9846        0.0401  0.0470
     13        0.0218       0.9956        0.0181  0.0500
     14        0.0151       0.9956        0.0140  0.0480
     15        0.0118       0.9956        0.0117  0.0470
     16        0.0094       0.9956        0.0104  0.0460
     17        0.0078       0.9967        0.0087  0.0450
     18        0.0065       0.9978        0.0072  0.0470
     19        0.0055       0.9

      9        0.0472       0.9945        0.0502  0.0510
     10        0.0591       0.8549        0.3523  0.0500
     11        0.1208       0.9714        0.0691  0.0490
     12        0.0735       0.9648        0.0666  0.0480
     13        0.0623       0.9868        0.0517  0.0440
     14        0.0457       0.9956        0.0452  0.0460
     15        0.0401       0.9956        0.0390  0.0490
     16        0.0365       0.9956        0.0353  0.0470
     17        0.0329       0.9978        0.0338  0.0450
     18        0.0346       0.9967        0.0387  0.0480
     19        0.0481       0.9066        0.2375  0.0450
     20        0.1263       0.9637        0.1215  0.0450
     21        0.0763       0.9813        0.0487  0.0450
     22        0.0589       0.9912        0.0423  0.0500
     23        0.0394       0.9912        0.0417  0.0540
     24        0.0307       0.9945        0.0327  0.0450
     25        0.0276       0.9978        0.0285  0.0480
     26        0.0271       0.9

     32        0.0263       0.9989        0.0260  0.0440
     33        0.0295       1.0000        0.0292  0.0510
     34        0.3152       0.6055        0.7297  0.0460
     35        0.4609       0.8670        0.3439  0.0470
     36        0.3107       0.9000        0.2572  0.0440
     37        0.2151       0.8956        0.2023  0.0500
     38        0.1521       0.9330        0.1487  0.0470
     39        0.1336       0.9330        0.1560  0.0440
     40        0.1319       0.9088        0.2294  0.0470
     41        0.1475       0.9352        0.1375  0.0480
     42        0.1406       0.9385        0.1494  0.0480
     43        0.1105       0.9571        0.1120  0.0470
     44        0.0962       0.9626        0.1026  0.0460
     45        0.0839       0.9275        0.1686  0.0450
     46        0.1092       0.9538        0.0962  0.0440
     47        0.0762       0.9637        0.0961  0.0460
     48        0.0868       0.8692        0.2690  0.0440
     49        0.2275       0.9

     38        0.3318       0.8396        0.3793  0.0460
     39        0.3260       0.8615        0.3509  0.0430
     40        0.3177       0.8956        0.3064  0.0460
     41        0.3280       0.8462        0.3652  0.0430
     42        0.3265       0.8560        0.3614  0.0460
     43        0.3246       0.8681        0.3375  0.0440
     44        0.3284       0.8418        0.3717  0.0440
     45        0.3268       0.8571        0.3583  0.0500
     46        0.3249       0.8670        0.3411  0.0460
     47        0.3295       0.8473        0.3691  0.0480
     48        0.3262       0.8604        0.3551  0.0480
     49        0.3251       0.8670        0.3422  0.0450
     50        0.3284       0.8462        0.3705  0.0470
  epoch    train_loss    valid_acc    valid_loss     dur
-------  ------------  -----------  ------------  ------
      1        0.6334       0.8319        0.5075  0.0470
      2        0.3673       0.8978        0.2969  0.0480
      3        0.2863       0.9

In [11]:
from skorch.callbacks import EarlyStopping

In [43]:
net_final = NeuralNetBinaryClassifier(
    MLP_network,
    train_split=None,
    criterion=torch.nn.BCEWithLogitsLoss,
    optimizer=torch.optim.SGD,
    optimizer__momentum=0.9, # momentum set to commonly used value to save CPU time
    batch_size=64, 
    max_epochs=40, 
    module__hidden_dim=10,
    optimizer__lr=0.01,
    optimizer__weight_decay=0.001
)

In [44]:
sm = SMOTE(random_state=42)
X_res, y_res = sm.fit_resample(X_train, y_train)

In [45]:
net_final.fit(X_res, y_res)

  epoch    train_loss     dur
-------  ------------  ------
      1        0.2256  4.6621
      2        0.2652  4.5435
      3        0.3096  4.5486
      4        0.3096  4.5235
      5        0.3096  4.5610
      6        0.3096  4.6406
      7        0.3096  4.5671
      8        0.3096  4.5674
      9        0.3096  4.5155
     10        0.3096  4.5050
     11        0.3096  4.5038
     12        0.3096  4.5391
     13        0.3096  4.5030
     14        0.3096  4.5572
     15        0.3096  4.5706
     16        0.3096  4.5130
     17        0.3096  4.5071
     18        0.3096  4.5370
     19        0.3096  4.5410
     20        0.3024  4.5060
     21        0.3096  4.5360
     22        0.3096  4.5390
     23        0.3096  4.4620
     24        0.3096  4.5180
     25        0.3096  4.4910
     26        0.3096  4.5190
     27        0.3096  4.4990
     28        0.3096  4.5060
     29        0.3096  4.5270
     30        0.3096  4.4780
     31        0.3096  4.4790
     32   

<class 'skorch.classifier.NeuralNetBinaryClassifier'>[initialized](
  module_=MLP_network(
    (output): Sequential(
      (0): Linear(in_features=21, out_features=10, bias=True)
      (1): ReLU()
      (2): Linear(in_features=10, out_features=1, bias=True)
    )
  ),
)

In [46]:
net_final.score(X_test, y_test)

0.15758698622937034